In [6]:
from sklearn.preprocessing import StandardScaler
from sklearn.linear_model import LinearRegression, Ridge, Lasso, RidgeCV, LassoCV, ElasticNet, ElasticNetCV
import statsmodels.api as sm
from sklearn.model_selection import train_test_split
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
from pandas_profiling import ProfileReport


In [4]:
dataset = pd.read_csv('https://raw.githubusercontent.com/naveenmnav/MachineLearning/main/Basic/AdmissionPrediction/Admission_Predict.csv')

In [5]:
dataset

Serial No.  GRE Score  TOEFL Score  University Rating  SOP  LOR   CGPA  \
0             1        337          118                  4  4.5   4.5  9.65   
1             2        324          107                  4  4.0   4.5  8.87   
2             3        316          104                  3  3.0   3.5  8.00   
3             4        322          110                  3  3.5   2.5  8.67   
4             5        314          103                  2  2.0   3.0  8.21   
..          ...        ...          ...                ...  ...   ...   ...   
395         396        324          110                  3  3.5   3.5  9.04   
396         397        325          107                  3  3.0   3.5  9.11   
397         398        330          116                  4  5.0   4.5  9.45   
398         399        312          103                  3  3.5   4.0  8.78   
399         400        333          117                  4  5.0   4.0  9.66   

     Research  Chance of Admit   
0           1              0.92  
1           1              0.76  
2           1              0.72  
3           1              0.80  
4           0              0.65  
..        ...               ...  
395         1              0.82  
396         1              0.84  
397         1              0.91  
398         0              0.67  
399         1              0.95  

[400 rows x 9 columns]

In [9]:
pf = ProfileReport(dataset)

In [12]:
pf.to_notebook_iframe()

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

### 1. Check Null Value

In [13]:
# Feature Pre Processing

dataset['GRE Score'] = dataset['GRE Score'].fillna(dataset['GRE Score'].mean())

In [14]:
dataset['TOEFL Score'] = dataset['TOEFL Score'].fillna(dataset['TOEFL Score'].mean())

In [18]:
dataset['University Rating'] = dataset['University Rating'].fillna(dataset['University Rating'].mean())

In [20]:
dataset.isnull().sum()

Serial No.           0
GRE Score            0
TOEFL Score          0
University Rating    0
SOP                  0
LOR                  0
CGPA                 0
Research             0
Chance of Admit      0
dtype: int64

In [22]:
dataset.drop(columns = ['Serial No.'], inplace = True)

In [23]:
dataset

GRE Score  TOEFL Score  University Rating  SOP  LOR   CGPA  Research  \
0          337          118                  4  4.5   4.5  9.65         1   
1          324          107                  4  4.0   4.5  8.87         1   
2          316          104                  3  3.0   3.5  8.00         1   
3          322          110                  3  3.5   2.5  8.67         1   
4          314          103                  2  2.0   3.0  8.21         0   
..         ...          ...                ...  ...   ...   ...       ...   
395        324          110                  3  3.5   3.5  9.04         1   
396        325          107                  3  3.0   3.5  9.11         1   
397        330          116                  4  5.0   4.5  9.45         1   
398        312          103                  3  3.5   4.0  8.78         0   
399        333          117                  4  5.0   4.0  9.66         1   

     Chance of Admit   
0                0.92  
1                0.76  
2                0.72  
3                0.80  
4                0.65  
..                ...  
395              0.82  
396              0.84  
397              0.91  
398              0.67  
399              0.95  

[400 rows x 8 columns]

In [29]:
y = dataset.iloc[:,-1]

In [30]:
y

0      0.92
1      0.76
2      0.72
3      0.80
4      0.65
       ... 
395    0.82
396    0.84
397    0.91
398    0.67
399    0.95
Name: Chance of Admit , Length: 400, dtype: float64

In [37]:
x = dataset.iloc[:,:-1]

In [38]:
x

GRE Score  TOEFL Score  University Rating  SOP  LOR   CGPA  Research
0          337          118                  4  4.5   4.5  9.65         1
1          324          107                  4  4.0   4.5  8.87         1
2          316          104                  3  3.0   3.5  8.00         1
3          322          110                  3  3.5   2.5  8.67         1
4          314          103                  2  2.0   3.0  8.21         0
..         ...          ...                ...  ...   ...   ...       ...
395        324          110                  3  3.5   3.5  9.04         1
396        325          107                  3  3.0   3.5  9.11         1
397        330          116                  4  5.0   4.5  9.45         1
398        312          103                  3  3.5   4.0  8.78         0
399        333          117                  4  5.0   4.0  9.66         1

[400 rows x 7 columns]

### 2.Scaling 
#### Using Standard Scaler

In [39]:
scaler = StandardScaler()

In [40]:
df = scaler.fit_transform(x)

In [41]:
df

array([[ 1.76210664,  1.74697064,  0.79882862, ...,  1.16732114,
         1.76481828,  0.90911166],
       [ 0.62765641, -0.06763531,  0.79882862, ...,  1.16732114,
         0.45515126,  0.90911166],
       [-0.07046681, -0.56252785, -0.07660001, ...,  0.05293342,
        -1.00563118,  0.90911166],
       ...,
       [ 1.15124883,  1.41704229,  0.79882862, ...,  1.16732114,
         1.42900622,  0.90911166],
       [-0.41952842, -0.72749202, -0.07660001, ...,  0.61012728,
         0.30403584, -1.09997489],
       [ 1.41304503,  1.58200646,  0.79882862, ...,  0.61012728,
         1.78160888,  0.90911166]])

### 3. Multicollinearity

2 ways :
1. Pearson
2. VIF -> Should be less than 10, we do not drop columns

In [44]:
from statsmodels.stats.outliers_influence import variance_inflation_factor

In [48]:
vif_info = pd.DataFrame()

In [49]:
vif_info['value'] =  [variance_inflation_factor(df,i) for i in range(df.shape[1])]

In [50]:
vif_info['feature']  = x.columns

In [51]:
vif_info

value            feature
0  4.615516          GRE Score
1  4.288959        TOEFL Score
2  2.919606  University Rating
3  3.075504                SOP
4  2.431258               LOR 
5  5.207403               CGPA
6  1.543312           Research

### 4. Train Test split

In [89]:
X_train, X_test, y_train, y_test = train_test_split(x,y, test_size = 0.15 , random_state = 100)

### 5. Linear Regression

In [90]:
lr = LinearRegression()

In [91]:
lr.fit(X_train, y_train)

LinearRegression()

In [92]:
lr.predict(X_test)

array([0.79750295, 0.75466362, 0.8653804 , 0.88622745, 0.67482272,
       0.85694783, 0.66517198, 0.74551816, 0.9068612 , 0.58198711,
       0.69061893, 0.70516061, 0.63791658, 0.67991398, 0.6155645 ,
       0.6623154 , 0.85738382, 0.60574268, 0.57900248, 0.83448663,
       0.6311833 , 0.84969236, 0.49961622, 0.80929399, 0.46987944,
       0.73970837, 0.7401726 , 0.78502555, 0.53630067, 0.96079275,
       0.89505117, 0.78001555, 0.72970071, 0.70756653, 0.55367142,
       0.52402231, 0.59361332, 0.74303983, 0.92353098, 0.48409195,
       0.67188849, 0.65138134, 0.77910193, 0.59480173, 0.78126798,
       0.41895286, 0.61742971, 0.88132453, 0.55729268, 0.57241871,
       0.93347553, 0.67981575, 0.82655084, 0.80241801, 0.74094733,
       0.8544475 , 0.42811782, 0.69337416, 0.77527867, 0.70065974])

In [93]:
## r2 value

### Accuracy
    
lr.score(X_test, y_test)

0.8548106878603849

In [94]:
def adj_r2(x,y):
    r2 = lr.score(x,y)
    n = x.shape[0]
    p = x.shape[1]
    ar2 = 1-(1-r2)*(n-1)/(n-p-1)
    return ar2

In [95]:
adj_r2(X_test, y_test)

0.8352659727646675

In [96]:
lr.coef_

array([ 0.00136208,  0.0033602 ,  0.00658657, -0.0039759 ,  0.02079406,
        0.12267578,  0.02826045])

In [97]:
lr.intercept_

-1.2188475807807624

In [98]:
## y =  0.00136208x1 + 0.0033602x2 + 0.00658657x3 -0.0039759 x4+  0.02079406 x5+ 0.12267578x6 +  0.02826045x7 + (-1.2188475807807624)

### 6. Lasso

In [99]:
lassocv = LassoCV(alphas = None, cv = 5, max_iter = 50000000, normalize = True)

In [101]:
lassocv.fit(X_train, y_train)

c:\users\naveen\appdata\local\programs\python\python37\lib\site-packages\sklearn\linear_model\_base.py:145: FutureWarning: 'normalize' was deprecated in version 1.0 and will be removed in 1.2.
If you wish to scale the data, use Pipeline with a StandardScaler in a preprocessing stage. To reproduce the previous behavior:

from sklearn.pipeline import make_pipeline

model = make_pipeline(StandardScaler(with_mean=False), Lasso())

If you wish to pass a sample_weight parameter, you need to pass it as a fit parameter to each step of the pipeline as follows:

kwargs = {s[0] + '__sample_weight': sample_weight for s in model.steps}
model.fit(X, y, **kwargs)

Set parameter alpha to: original_alpha * np.sqrt(n_samples). 
  FutureWarning,


LassoCV(cv=5, max_iter=50000000, normalize=True)

In [102]:
lassocv.alpha_

0.00011821657566050382

In [104]:
lasso_regression = Lasso(alpha = lassocv.alpha_)

In [105]:
lasso_regression.fit(X_train, y_train)

Lasso(alpha=0.00011821657566050382)

In [107]:
lasso_regression.score(X_test, y_test)

0.85553818713825

#### Lasso's accuracy is greater than Linear

#### Ridge Regression

In [114]:
ridgecv = RidgeCV(alphas = np.random.uniform(0,10,500), cv = 10, normalize = True)

In [115]:
ridgecv.fit(X_train, y_train)

c:\users\naveen\appdata\local\programs\python\python37\lib\site-packages\sklearn\linear_model\_base.py:145: FutureWarning: 'normalize' was deprecated in version 1.0 and will be removed in 1.2.
If you wish to scale the data, use Pipeline with a StandardScaler in a preprocessing stage. To reproduce the previous behavior:

from sklearn.pipeline import make_pipeline

model = make_pipeline(StandardScaler(with_mean=False), Ridge())

If you wish to pass a sample_weight parameter, you need to pass it as a fit parameter to each step of the pipeline as follows:

kwargs = {s[0] + '__sample_weight': sample_weight for s in model.steps}
model.fit(X, y, **kwargs)

Set parameter alpha to: original_alpha * n_samples. 
  FutureWarning,
c:\users\naveen\appdata\local\programs\python\python37\lib\site-packages\sklearn\linear_model\_base.py:145: FutureWarning: 'normalize' was deprecated in version 1.0 and will be removed in 1.2.
If you wish to scale the data, use Pipeline with a StandardScaler in a preproce

c:\users\naveen\appdata\local\programs\python\python37\lib\site-packages\sklearn\linear_model\_base.py:145: FutureWarning: 'normalize' was deprecated in version 1.0 and will be removed in 1.2.
If you wish to scale the data, use Pipeline with a StandardScaler in a preprocessing stage. To reproduce the previous behavior:

from sklearn.pipeline import make_pipeline

model = make_pipeline(StandardScaler(with_mean=False), Ridge())

If you wish to pass a sample_weight parameter, you need to pass it as a fit parameter to each step of the pipeline as follows:

kwargs = {s[0] + '__sample_weight': sample_weight for s in model.steps}
model.fit(X, y, **kwargs)

Set parameter alpha to: original_alpha * n_samples. 
  FutureWarning,
c:\users\naveen\appdata\local\programs\python\python37\lib\site-packages\sklearn\linear_model\_base.py:145: FutureWarning: 'normalize' was deprecated in version 1.0 and will be removed in 1.2.
If you wish to scale the data, use Pipeline with a StandardScaler in a preproce

c:\users\naveen\appdata\local\programs\python\python37\lib\site-packages\sklearn\linear_model\_base.py:145: FutureWarning: 'normalize' was deprecated in version 1.0 and will be removed in 1.2.
If you wish to scale the data, use Pipeline with a StandardScaler in a preprocessing stage. To reproduce the previous behavior:

from sklearn.pipeline import make_pipeline

model = make_pipeline(StandardScaler(with_mean=False), Ridge())

If you wish to pass a sample_weight parameter, you need to pass it as a fit parameter to each step of the pipeline as follows:

kwargs = {s[0] + '__sample_weight': sample_weight for s in model.steps}
model.fit(X, y, **kwargs)

Set parameter alpha to: original_alpha * n_samples. 
  FutureWarning,
c:\users\naveen\appdata\local\programs\python\python37\lib\site-packages\sklearn\linear_model\_base.py:145: FutureWarning: 'normalize' was deprecated in version 1.0 and will be removed in 1.2.
If you wish to scale the data, use Pipeline with a StandardScaler in a preproce

c:\users\naveen\appdata\local\programs\python\python37\lib\site-packages\sklearn\linear_model\_base.py:145: FutureWarning: 'normalize' was deprecated in version 1.0 and will be removed in 1.2.
If you wish to scale the data, use Pipeline with a StandardScaler in a preprocessing stage. To reproduce the previous behavior:

from sklearn.pipeline import make_pipeline

model = make_pipeline(StandardScaler(with_mean=False), Ridge())

If you wish to pass a sample_weight parameter, you need to pass it as a fit parameter to each step of the pipeline as follows:

kwargs = {s[0] + '__sample_weight': sample_weight for s in model.steps}
model.fit(X, y, **kwargs)

Set parameter alpha to: original_alpha * n_samples. 
  FutureWarning,
c:\users\naveen\appdata\local\programs\python\python37\lib\site-packages\sklearn\linear_model\_base.py:145: FutureWarning: 'normalize' was deprecated in version 1.0 and will be removed in 1.2.
If you wish to scale the data, use Pipeline with a StandardScaler in a preproce

c:\users\naveen\appdata\local\programs\python\python37\lib\site-packages\sklearn\linear_model\_base.py:145: FutureWarning: 'normalize' was deprecated in version 1.0 and will be removed in 1.2.
If you wish to scale the data, use Pipeline with a StandardScaler in a preprocessing stage. To reproduce the previous behavior:

from sklearn.pipeline import make_pipeline

model = make_pipeline(StandardScaler(with_mean=False), Ridge())

If you wish to pass a sample_weight parameter, you need to pass it as a fit parameter to each step of the pipeline as follows:

kwargs = {s[0] + '__sample_weight': sample_weight for s in model.steps}
model.fit(X, y, **kwargs)

Set parameter alpha to: original_alpha * n_samples. 
  FutureWarning,
c:\users\naveen\appdata\local\programs\python\python37\lib\site-packages\sklearn\linear_model\_base.py:145: FutureWarning: 'normalize' was deprecated in version 1.0 and will be removed in 1.2.
If you wish to scale the data, use Pipeline with a StandardScaler in a preproce

...

c:\users\naveen\appdata\local\programs\python\python37\lib\site-packages\sklearn\linear_model\_base.py:145: FutureWarning: 'normalize' was deprecated in version 1.0 and will be removed in 1.2.
If you wish to scale the data, use Pipeline with a StandardScaler in a preprocessing stage. To reproduce the previous behavior:

from sklearn.pipeline import make_pipeline

model = make_pipeline(StandardScaler(with_mean=False), Ridge())

If you wish to pass a sample_weight parameter, you need to pass it as a fit parameter to each step of the pipeline as follows:

kwargs = {s[0] + '__sample_weight': sample_weight for s in model.steps}
model.fit(X, y, **kwargs)

Set parameter alpha to: original_alpha * n_samples. 
  FutureWarning,
c:\users\naveen\appdata\local\programs\python\python37\lib\site-packages\sklearn\linear_model\_base.py:145: FutureWarning: 'normalize' was deprecated in version 1.0 and will be removed in 1.2.
If you wish to scale the data, use Pipeline with a StandardScaler in a preproce

c:\users\naveen\appdata\local\programs\python\python37\lib\site-packages\sklearn\linear_model\_base.py:145: FutureWarning: 'normalize' was deprecated in version 1.0 and will be removed in 1.2.
If you wish to scale the data, use Pipeline with a StandardScaler in a preprocessing stage. To reproduce the previous behavior:

from sklearn.pipeline import make_pipeline

model = make_pipeline(StandardScaler(with_mean=False), Ridge())

If you wish to pass a sample_weight parameter, you need to pass it as a fit parameter to each step of the pipeline as follows:

kwargs = {s[0] + '__sample_weight': sample_weight for s in model.steps}
model.fit(X, y, **kwargs)

Set parameter alpha to: original_alpha * n_samples. 
  FutureWarning,
c:\users\naveen\appdata\local\programs\python\python37\lib\site-packages\sklearn\linear_model\_base.py:145: FutureWarning: 'normalize' was deprecated in version 1.0 and will be removed in 1.2.
If you wish to scale the data, use Pipeline with a StandardScaler in a preproce

c:\users\naveen\appdata\local\programs\python\python37\lib\site-packages\sklearn\linear_model\_base.py:145: FutureWarning: 'normalize' was deprecated in version 1.0 and will be removed in 1.2.
If you wish to scale the data, use Pipeline with a StandardScaler in a preprocessing stage. To reproduce the previous behavior:

from sklearn.pipeline import make_pipeline

model = make_pipeline(StandardScaler(with_mean=False), Ridge())

If you wish to pass a sample_weight parameter, you need to pass it as a fit parameter to each step of the pipeline as follows:

kwargs = {s[0] + '__sample_weight': sample_weight for s in model.steps}
model.fit(X, y, **kwargs)

Set parameter alpha to: original_alpha * n_samples. 
  FutureWarning,
c:\users\naveen\appdata\local\programs\python\python37\lib\site-packages\sklearn\linear_model\_base.py:145: FutureWarning: 'normalize' was deprecated in version 1.0 and will be removed in 1.2.
If you wish to scale the data, use Pipeline with a StandardScaler in a preproce

c:\users\naveen\appdata\local\programs\python\python37\lib\site-packages\sklearn\linear_model\_base.py:145: FutureWarning: 'normalize' was deprecated in version 1.0 and will be removed in 1.2.
If you wish to scale the data, use Pipeline with a StandardScaler in a preprocessing stage. To reproduce the previous behavior:

from sklearn.pipeline import make_pipeline

model = make_pipeline(StandardScaler(with_mean=False), Ridge())

If you wish to pass a sample_weight parameter, you need to pass it as a fit parameter to each step of the pipeline as follows:

kwargs = {s[0] + '__sample_weight': sample_weight for s in model.steps}
model.fit(X, y, **kwargs)

Set parameter alpha to: original_alpha * n_samples. 
  FutureWarning,
c:\users\naveen\appdata\local\programs\python\python37\lib\site-packages\sklearn\linear_model\_base.py:145: FutureWarning: 'normalize' was deprecated in version 1.0 and will be removed in 1.2.
If you wish to scale the data, use Pipeline with a StandardScaler in a preproce

RidgeCV(alphas=array([9.50461165, 7.60430012, 2.68400227, 7.59337035, 5.94370205,
       7.95415416, 4.5370853 , 0.19288937, 6.45893738, 2.84628983,
       0.22374244, 1.84802738, 0.91290519, 0.64559338, 1.52214422,
       3.00949675, 6.16261544, 3.09190098, 5.43776808, 3.65776125,
       8.79368956, 7.72269934, 9.63007275, 4.56486583, 4.6476723 ,
       3.67937795, 4.24262368, 4.60695349, 0.23731706, 1.4564786 ,
       2...
       5.63518865, 9.65392659, 1.92282614, 1.32160304, 3.52507387,
       9.27292714, 8.48938105, 5.10161951, 1.32676226, 5.53442467,
       0.37108018, 9.98065444, 4.58242805, 6.14568455, 8.58793214,
       2.99744899, 3.7235136 , 5.10736742, 0.97215269, 4.78051026,
       5.69275625, 4.93398726, 5.81364353, 3.45991298, 8.56443011,
       5.93393761, 5.27123602, 0.10233064, 3.51792997, 3.51031803]),
        cv=10, normalize=True)

In [116]:
ridgecv.alpha_

0.05613815986232895

In [119]:
ridge_regression = Ridge(alpha = ridgecv.alpha_)
ridge_regression.fit(X_train, y_train)

Ridge(alpha=0.05613815986232895)

In [120]:
ridge_regression.score(X_test, y_test)

0.8548857552384176

#### Ridge is accurate than both Lasso and Linear

In [121]:
el = ElasticNetCV(alphas = None, cv = 10)
el.fit(X_test, y_test)

ElasticNetCV(cv=10)

In [122]:
el.alpha_

0.003939286696476961

In [124]:
el.l1_ratio_

0.5

In [127]:
elasticnet_reg = ElasticNet(alpha = el.alpha_, l1_ratio = el.l1_ratio_)

In [128]:
elasticnet_reg.fit(X_train, y_train)

ElasticNet(alpha=0.003939286696476961)

In [129]:
elasticnet_reg.score(X_test, y_test)

0.8600745332552966